# Datacenter Score Analysis

This notebook ingests recent market and weather data to compute a composite datacenter siting score across U.S. grid regions.

## Environment Setup
Ensure required dependencies are available for the workflow.

## Imports and Global Configuration


In [1]:
import json
import os
from datetime import datetime, timedelta
from functools import lru_cache
from pathlib import Path

import numpy as np
import pandas as pd
import requests
import plotly.express as px
import matplotlib.pyplot as plt
from prophet import Prophet

plt.style.use('seaborn-v0_8')
px.defaults.template = 'plotly_white'

CACHE_DIR = Path('cache')
CACHE_DIR.mkdir(exist_ok=True)
EIA_BASE_URL = 'https://api.eia.gov/v2/electricity/rto/region-data/data/'
EIA_API_KEY = os.getenv('EIA_API_KEY')
HISTORICAL_DAYS = 90
PROPHET_LOOKBACK_DAYS = 60
FORECAST_HOURS = 24 * 7


## EIA Hourly Demand Fetching


In [2]:
def _cache_path_for_region(region: str) -> Path:
    return CACHE_DIR / f'eia_{region.lower()}_hourly.csv'


@lru_cache(maxsize=None)
def fetch_eia_hourly(region: str) -> pd.DataFrame:
    """Fetch the most recent 90 days of hourly demand for the requested EIA region.

    Parameters
    ----------
    region : str
        The EIA RTO/region code (e.g., 'CAL', 'TEX').

    Returns
    -------
    pd.DataFrame
        DataFrame with columns [datetime, demand_MW, region].
    """
    cache_path = _cache_path_for_region(region)
    end = datetime.utcnow()
    start = end - timedelta(days=HISTORICAL_DAYS)
    params = {
        'api_key': EIA_API_KEY,
        'data[0]': 'value',
        'facets[respondent][]': region,
        'frequency': 'hourly',
        'start': start.strftime('%Y-%m-%dT%H'),
        'end': end.strftime('%Y-%m-%dT%H'),
        'sort[0][column]': 'period',
        'sort[0][direction]': 'desc',
        'offset': 0,
        'length': 5000,
    }
    try:
        response = requests.get(EIA_BASE_URL, params=params, timeout=30)
        response.raise_for_status()
        payload = response.json()
        data = payload.get('response', {}).get('data', [])
        if not data:
            raise ValueError('Empty dataset returned from EIA API.')
        records = []
        for item in data:
            period = item.get('period')
            value = item.get('value')
            if period is None or value is None:
                continue
            records.append({
                'datetime': pd.to_datetime(period),
                'demand_MW': float(value),
                'region': region,
            })
        df = pd.DataFrame(records)
        if df.empty:
            raise ValueError('No valid records parsed from EIA response.')
        df = df.drop_duplicates(subset='datetime').sort_values('datetime')
        df = df[df['datetime'] >= start]
        df.to_csv(cache_path, index=False)
        return df
    except Exception as exc:
        print(f'EIA API fetch failed for {region}: {exc}')
        if cache_path.exists():
            print(f'Loading cached data for {region} from {cache_path}.')
            df = pd.read_csv(cache_path, parse_dates=['datetime'])
            return df
        raise


## Forecasting and Grid Metrics


In [3]:
def _prepare_hourly_series(df_region: pd.DataFrame) -> pd.DataFrame:
    if df_region.empty:
        raise ValueError('Region dataframe is empty.')
    df = df_region.copy()
    df = df.drop_duplicates(subset='datetime').sort_values('datetime')
    df = df.set_index('datetime')
    full_range = pd.date_range(df.index.min(), df.index.max(), freq='H')
    df = df.reindex(full_range)
    df['demand_MW'] = df['demand_MW'].interpolate(method='time')
    df['region'] = df_region['region'].iloc[0]
    return df


def forecast_peak_demand(df_region: pd.DataFrame) -> float:
    prepped = _prepare_hourly_series(df_region)
    recent_start = prepped.index.max() - timedelta(days=PROPHET_LOOKBACK_DAYS)
    df_recent = prepped[prepped.index >= recent_start]
    prophet_df = df_recent.reset_index().rename(columns={'index': 'ds', 'demand_MW': 'y'})
    model = Prophet(
        growth='flat',
        daily_seasonality=True,
        weekly_seasonality=True,
        yearly_seasonality=False
    )
    model.add_country_holidays(country_name='US')
    model.fit(prophet_df)
    future = model.make_future_dataframe(periods=FORECAST_HOURS, freq='H', include_history=False)
    forecast = model.predict(future)
    peak_forecast = float(forecast['yhat'].max())
    return peak_forecast


def compute_volatility(df_region: pd.DataFrame) -> float:
    prepped = _prepare_hourly_series(df_region)
    rolling_std = prepped['demand_MW'].rolling(window=24, min_periods=1).std()
    return float(rolling_std.iloc[-1])


def compute_renewable_proxy(df_region: pd.DataFrame) -> float:
    prepped = _prepare_hourly_series(df_region)
    mean_load = prepped['demand_MW'].mean()
    return float(1.0 / (1.0 + mean_load))


def compute_carbon_proxy(renewable_proxy: float) -> float:
    return float(1.0 - renewable_proxy)


## Weather Data via Open-Meteo


In [4]:
@lru_cache(maxsize=None)
def fetch_temperature(lat: float, lon: float) -> float:
    url = 'https://api.open-meteo.com/v1/forecast'
    params = {
        'latitude': lat,
        'longitude': lon,
        'daily': 'temperature_2m_mean',
        'past_days': 60,
        'timezone': 'UTC',
    }
    try:
        response = requests.get(url, params=params, timeout=30)
        response.raise_for_status()
        data = response.json()
        temps = data.get('daily', {}).get('temperature_2m_mean', [])
        if not temps:
            raise ValueError('Temperature series is empty.')
        return float(np.mean(temps))
    except Exception as exc:
        print(f'Open-Meteo fetch failed for ({lat}, {lon}): {exc}')
        return float('nan')


region_coords = {
    'CAL': (36.5, -119.5),
    'CAR': (35.5, -80.0),
    'CENT': (38.5, -94.5),
    'FLA': (28.0, -82.0),
    'MIDA': (39.0, -77.0),
    'MIDW': (42.0, -89.0),
    'NE': (42.5, -72.5),
    'NY': (42.9, -75.3),
    'NW': (45.5, -120.5),
    'SE': (33.0, -84.0),
    'SW': (36.0, -111.5),
    'TEN': (36.0, -86.0),
    'TEX': (31.0, -99.0),
}


## Compute Datacenter Scores


In [6]:
records = []
for region, (lat, lon) in region_coords.items():
    try:
        df_region = fetch_eia_hourly(region)
    except Exception as exc:
        print(f'Skipping region {region} due to data issues: {exc}')
        continue
    df_region = df_region.sort_values('datetime')
    latest_demand = float(df_region['demand_MW'].iloc[-1]) if not df_region.empty else float('nan')
    volatility = compute_volatility(df_region)
    peak = forecast_peak_demand(df_region)
    renewable_proxy = compute_renewable_proxy(df_region)
    carbon_proxy = compute_carbon_proxy(renewable_proxy)
    avg_temp = fetch_temperature(lat, lon)
    records.append({
        'region': region,
        'price': latest_demand,
        'peak_forecast': peak,
        'volatility': volatility,
        'renewable_proxy': renewable_proxy,
        'carbon_proxy': carbon_proxy,
        'avg_temp': avg_temp,
        'lat': lat,
        'lon': lon,
    })

dc_df = pd.DataFrame(records)
if dc_df.empty:
    dc_df = pd.DataFrame(columns=['region', 'price', 'peak_forecast', 'volatility', 'renewable_proxy', 'carbon_proxy', 'avg_temp', 'lat', 'lon'])
else:
    metrics_to_normalize = {
        'price': 'price_norm',
        'peak_forecast': 'peak_norm',
        'volatility': 'volatility_norm',
        'renewable_proxy': 'renewable_norm',
        'carbon_proxy': 'carbon_norm',
        'avg_temp': 'temp_norm',
    }
    for metric, norm_col in metrics_to_normalize.items():
        col = dc_df[metric]
        col_min, col_max = col.min(), col.max()
        if np.isfinite(col_min) and np.isfinite(col_max) and col_max != col_min:
            dc_df[norm_col] = (col - col_min) / (col_max - col_min)
        else:
            dc_df[norm_col] = 0.0
    dc_df['profitability'] = (
        0.40 * (1 - dc_df['price_norm']) +
        0.30 * (1 - dc_df['peak_norm']) +
        0.30 * (1 - dc_df['volatility_norm'])
    )
    dc_df['sustainability'] = (
        0.35 * dc_df['renewable_norm'] +
        0.30 * (1 - dc_df['carbon_norm']) +
        0.20 * (1 - dc_df['temp_norm']) +
        0.15 * dc_df['renewable_norm']
    )
    dc_df['hybrid'] = 0.5 * dc_df['profitability'] + 0.5 * dc_df['sustainability']
    dc_df = dc_df.sort_values('hybrid', ascending=False).reset_index(drop=True)

final_columns = ['region', 'price', 'peak_forecast', 'volatility', 'renewable_proxy', 'carbon_proxy', 'avg_temp', 'profitability', 'sustainability', 'hybrid', 'lat', 'lon']
for col in final_columns:
    if col not in dc_df.columns:
        dc_df[col] = np.nan
dc_df_final = dc_df[final_columns]
dc_df_final.to_csv('datacenter_scores.csv', index=False)
dc_df_final

/var/folders/h3/f3_68x516pj6d7h2119r5st00000gn/T/ipykernel_87653/271384653.py:7: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  full_range = pd.date_range(df.index.min(), df.index.max(), freq='H')
/var/folders/h3/f3_68x516pj6d7h2119r5st00000gn/T/ipykernel_87653/271384653.py:7: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  full_range = pd.date_range(df.index.min(), df.index.max(), freq='H')
16:12:26 - cmdstanpy - INFO - Chain [1] start processing
16:12:26 - cmdstanpy - INFO - Chain [1] done processing
/Library/Frameworks/Python.framework/Versions/3.13/lib/python3.13/site-packages/prophet/forecaster.py:1872: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  dates = pd.date_range(
/Library/Frameworks/Python.framework/Versions/3.13/lib/python3.13/site-packages/prophet/forecaster.py:1418: RuntimeWarning: divide by zero encountered in ma

region    price  peak_forecast   volatility  renewable_proxy  carbon_proxy  \
0      NE  15290.0   14816.108705  1259.619818         0.000084      0.999916   
1      SW  13539.0   16169.996122  1184.922194         0.000076      0.999924   
2      NY  18331.0   18637.028604  1493.486930         0.000064      0.999936   
3     TEN  17917.0   20105.060194   975.489553         0.000058      0.999942   
4     CAR  21985.0   27519.625856  2102.078174         0.000043      0.999957   
5      SE  25366.0   29296.602898  1690.648147         0.000041      0.999959   
6     CAL  30783.0   35397.679667  2484.218790         0.000033      0.999967   
7    CENT  35976.0   35384.518476  2388.887310         0.000032      0.999968   
8     FLA  26560.0   37990.821407  3374.582331         0.000034      0.999966   
9      NW  40142.0   43732.176558  3323.070974         0.000026      0.999974   
10    TEX  57224.0   66727.109470  5439.557263         0.000019      0.999981   
11   MIDW  76489.0   87169.597979  4085.563713         0.000013      0.999987   
12   MIDA  92340.0   98306.491728  4194.443529         0.000012      0.999988   

     avg_temp  profitability  sustainability    hybrid   lat    lon  
0   10.110448       0.972017        0.974974  0.973495  42.5  -72.5  
1   14.217910       0.981061        0.829280  0.905170  36.0 -111.5  
2    8.340299       0.927135        0.780653  0.853894  42.9  -75.3  
3   16.353731       0.958773        0.592675  0.775724  36.0  -86.0  
4   16.052239       0.835770        0.439196  0.637483  35.5  -80.0  
5   17.505970       0.839873        0.389647  0.614760  33.0  -84.0  
6   18.297015       0.737122        0.291777  0.514449  36.5 -119.5  
7   16.079104       0.717216        0.309630  0.513423  38.5  -94.5  
8   22.486567       0.689405        0.244330  0.466868  28.0  -82.0  
9   10.828358       0.603294        0.319142  0.461218  45.5 -120.5  
10  21.695522       0.291723        0.087670  0.189697  31.0  -99.0  
11  12.549254       0.211471        0.157612  0.184541  42.0  -89.0  
12  14.243284       0.083676        0.116544  0.100110  39.0  -77.0

## Visualize Scores


In [7]:
if not dc_df_final.empty:
    melted = dc_df_final.melt(id_vars=['region'], value_vars=['profitability', 'sustainability', 'hybrid'], var_name='metric', value_name='score')
    fig = px.bar(melted, x='region', y='score', color='metric', barmode='group', title='Datacenter Score Components by Region')
    fig.show()
else:
    print('No data available for bar chart visualization.')


In [8]:
dc_df_final

region    price  peak_forecast   volatility  renewable_proxy  carbon_proxy  \
0      NE  15290.0   14816.108705  1259.619818         0.000084      0.999916   
1      SW  13539.0   16169.996122  1184.922194         0.000076      0.999924   
2      NY  18331.0   18637.028604  1493.486930         0.000064      0.999936   
3     TEN  17917.0   20105.060194   975.489553         0.000058      0.999942   
4     CAR  21985.0   27519.625856  2102.078174         0.000043      0.999957   
5      SE  25366.0   29296.602898  1690.648147         0.000041      0.999959   
6     CAL  30783.0   35397.679667  2484.218790         0.000033      0.999967   
7    CENT  35976.0   35384.518476  2388.887310         0.000032      0.999968   
8     FLA  26560.0   37990.821407  3374.582331         0.000034      0.999966   
9      NW  40142.0   43732.176558  3323.070974         0.000026      0.999974   
10    TEX  57224.0   66727.109470  5439.557263         0.000019      0.999981   
11   MIDW  76489.0   87169.597979  4085.563713         0.000013      0.999987   
12   MIDA  92340.0   98306.491728  4194.443529         0.000012      0.999988   

     avg_temp  profitability  sustainability    hybrid   lat    lon  
0   10.110448       0.972017        0.974974  0.973495  42.5  -72.5  
1   14.217910       0.981061        0.829280  0.905170  36.0 -111.5  
2    8.340299       0.927135        0.780653  0.853894  42.9  -75.3  
3   16.353731       0.958773        0.592675  0.775724  36.0  -86.0  
4   16.052239       0.835770        0.439196  0.637483  35.5  -80.0  
5   17.505970       0.839873        0.389647  0.614760  33.0  -84.0  
6   18.297015       0.737122        0.291777  0.514449  36.5 -119.5  
7   16.079104       0.717216        0.309630  0.513423  38.5  -94.5  
8   22.486567       0.689405        0.244330  0.466868  28.0  -82.0  
9   10.828358       0.603294        0.319142  0.461218  45.5 -120.5  
10  21.695522       0.291723        0.087670  0.189697  31.0  -99.0  
11  12.549254       0.211471        0.157612  0.184541  42.0  -89.0  
12  14.243284       0.083676        0.116544  0.100110  39.0  -77.0

In [9]:
fig_map = px.scatter_geo(
    dc_df_final,
    lat='lat',
    lon='lon',
    size='hybrid',
    color='hybrid',
    hover_name='region',
    projection='albers usa',
    title='Hybrid Datacenter Score Across U.S. Grid Regions'
)
fig_map.show()

In [ ]:
import h3
import geopandas as gpd
from shapely.geometry import Polygon, mapping
import matplotlib
import folium
import mapclassify
from pathlib import Path
from zipfile import ZipFile

try:
    import geodatasets
except ImportError as exc:
    raise ImportError(
        "Install geodatasets>=2024.8.0 to access the Natural Earth outline:"
        " pip install geodatasets"
    ) from exc

HEX_RES = 4

land_zip = Path(geodatasets.get_path("naturalearth.land"))
land_dir = land_zip.with_suffix("")
if not land_dir.exists():
    with ZipFile(land_zip) as zf:
        zf.extractall(land_dir)

world = gpd.read_file(land_dir / "ne_110m_land.shp")
name_field = "ADMIN" if "ADMIN" in world.columns else "name"
us_geom = world.loc[world[name_field] == "United States of America", "geometry"].unary_union
if us_geom.is_empty:
    raise ValueError("United States geometry missing in Natural Earth dataset.")
us_geojson = mapping(us_geom)
h3_polygon = h3.polygon_to_cells(us_geojson, HEX_RES)

cells = []
for h in h3_polygon:
    boundary = h3.cell_to_boundary(h)
    poly = Polygon([(lng, lat) for lat, lng in boundary])
    cells.append({"h3": h, "geometry": poly})

grid_gdf = gpd.GeoDataFrame(cells, crs="EPSG:4326")

# Assign datacenter scores to each H3 cell (averaging duplicates)
dc_hex = dc_df_final.copy()
dc_hex["h3"] = dc_hex.apply(
    lambda row: h3.latlng_to_cell(row["lat"], row["lon"], HEX_RES), axis=1
)
hex_scores = (
    dc_hex.groupby("h3")
    .agg({"hybrid": "mean", "region": "first"})
    .reset_index()
)

gdf_hex = grid_gdf.merge(hex_scores, on="h3", how="left")

gdf_hex.explore(column="hybrid", cmap="YlOrRd", missing_kwds={"color": "#cccccc"})


KeyError: 'name'

In [56]:
import h3
import geopandas as gpd
from shapely.geometry import Polygon, box

HEX_RES = 4

# 1. US bounding box as shapely polygon
us_bounds = box(-125, 24, -66, 50)

# 2. Convert shapely coords to list of (lat, lng)
outer = [(lat, lng) for lng, lat in us_bounds.exterior.coords]

# 3. Build the H3 Polygon (outer ring only)
poly = h3.LatLngPoly(outer)

# 4. Generate hex cells within the polygon
h3_cells = h3.polygon_to_cells(poly, HEX_RES)

# 5. Convert to shapely polygons
hex_rows = []
for h in h3_cells:
    boundary = h3.cell_to_boundary(h)
    poly = Polygon([(lng, lat) for lat, lng in boundary])
    hex_rows.append({"h3": h, "geometry": poly})

# 6. Convert to GeoDataFrame
gdf_hex = gpd.GeoDataFrame(hex_rows, crs="EPSG:4326")
gdf_hex.explore()

In [ ]:
import geopandas as gpd
from shapely.geometry import Polygon
import numpy as np

# 1. Load USA polygon
usa = gpd.read_file(
    "https://raw.githubusercontent.com/PublicaMundi/MappingAPI/master/data/geojson/us-states.json"
)
usa_border = usa.unary_union
usa_gdf = gpd.GeoDataFrame(geometry=[usa_border], crs="EPSG:4326")

# 2. Reproject to Albers Equal Area (CRS suitable for USA)
usa_proj = usa_gdf.to_crs("EPSG:5070")  # NAD83 / Conus Albers

# 3. Hex size in METERS (50000 = 50 km hexes)
HEX_SIZE = 50000

def make_hex(x, y, size):
    """Make a perfect hexagon centered at (x,y) in projected coordinates."""
    angles = np.linspace(0, 2 * np.pi, 7)
    return Polygon([
        (x + size * np.cos(a), y + size * np.sin(a)) 
        for a in angles
    ])

# 4. Build bounding box in projected coordinates
minx, miny, maxx, maxy = usa_proj.total_bounds

# 5. Generate a hex grid in projected CRS
hexes = []
x = minx
row = 0

dx = HEX_SIZE * 3/2
dy = HEX_SIZE * np.sqrt(3) / 2

y = miny
while y < maxy + HEX_SIZE:
    x_offset = (row % 2) * (HEX_SIZE * 0.75)
    x = minx - HEX_SIZE
    while x < maxx + HEX_SIZE:
        hexes.append(make_hex(x + x_offset, y, HEX_SIZE))
        x += dx
    y += dy
    row += 1

hexgrid_proj = gpd.GeoDataFrame(geometry=hexes, crs="EPSG:5070")

# 6. Clip hexgrid to US border
hex_us_proj = gpd.overlay(hexgrid_proj, usa_proj, how="intersection")

# 7. Reproject back to WGS84 for Folium
hex_us = hex_us_proj.to_crs("EPSG:4326")

# 8. Plot
hex_us.explore()

/var/folders/h3/f3_68x516pj6d7h2119r5st00000gn/T/ipykernel_77918/554976437.py:9: DeprecationWarning:

The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.



In [ ]:
import geopandas as gpd
from shapely.geometry import Polygon
import numpy as np

# 1. Load USA polygon
usa = gpd.read_file(
    "https://raw.githubusercontent.com/PublicaMundi/MappingAPI/master/data/geojson/us-states.json"
)
usa_border = usa.unary_union
usa_gdf = gpd.GeoDataFrame(geometry=[usa_border], crs="EPSG:4326")

# 2. Reproject to Albers Equal Area (CRS suitable for USA)
usa_proj = usa_gdf.to_crs("EPSG:5070")  # NAD83 / Conus Albers

# 3. Hex radius in meters (distance from center to vertex)
HEX_RADIUS = 50000  # 50 km radius hex

def make_hex(center_x, center_y, radius):
    """Return a perfect pointy-top hexagon polygon with tiny overlap."""
    angles = np.radians(np.arange(30, 390, 60))
    # Add 0.1% overlap to ensure no gaps due to floating point precision
    overlap_factor = 1.001
    return Polygon([
        (center_x + radius * overlap_factor * np.cos(a), 
         center_y + radius * overlap_factor * np.sin(a))
        for a in angles
    ])

# --- Correct tiling spacing ---
hex_width = 2 * HEX_RADIUS                        # flat-to-flat width
hex_height = np.sqrt(3) * HEX_RADIUS              # point-to-point height

dx = np.sqrt(3) * HEX_RADIUS                             # horizontal spacing
dy = 0.865 * hex_height                                    # vertical spacing

# 4. Build bounding box in projected coordinates
minx, miny, maxx, maxy = usa_proj.total_bounds

# 5. Generate hex centers
hexes = []
row = 0
y = miny - hex_height

while y < maxy + hex_height:
    # offset every other row
    x_offset = (row % 2) * (dx / 2)  # = 0.75 * HEX_RADIUS
    x = minx - hex_width
    while x < maxx + hex_width:
        hexes.append(make_hex(x + x_offset, y, HEX_RADIUS))
        x += dx
    y += dy
    row += 1

hexgrid_proj = gpd.GeoDataFrame(geometry=hexes, crs="EPSG:5070")

# 6. Clip hexgrid to US border
hex_us_proj = gpd.overlay(hexgrid_proj, usa_proj, how="intersection")

# 7. Reproject back to WGS84 for Folium / display
hex_us = hex_us_proj.to_crs("EPSG:4326")

# 8. Visualize (geopandas)
hex_us.explore()

/var/folders/h3/f3_68x516pj6d7h2119r5st00000gn/T/ipykernel_77918/2202859732.py:9: DeprecationWarning:

The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.



In [103]:
# 1. Convert datacenters to GeoDataFrame
dc_points = gpd.GeoDataFrame(
    dc_df_final,
    geometry=gpd.points_from_xy(dc_df_final.lon, dc_df_final.lat),
    crs="EPSG:4326"
)

dc_points_proj = dc_points.to_crs("EPSG:5070")

# 2. Spatial join (assign each point to a hex)
dc_with_hex = gpd.sjoin(dc_points_proj, hexgrid_proj.reset_index(), how="left", predicate="within")

# 3. Average hybrid score per hex
hex_scores = dc_with_hex.groupby("index")["hybrid"].mean()

# 4. Attach scores to hex grid
hex_us_proj["hybrid"] = hex_us_proj.index.map(hex_scores)

# 5. Convert back to WGS84
hex_us = hex_us_proj.to_crs("EPSG:4326")

# 6. Visualize
hex_us.explore(
    column="hybrid",
    cmap="YlOrRd",
    missing_kwds={"color": "#cccccc", "label": "No datacenter nearby"},
    legend=True
)

In [104]:
import numpy as np

# Create predictor fields for each hex
hex_us_proj["temp"] = np.random.normal(loc=55, scale=12, size=len(hex_us_proj))          # Fahrenheit
hex_us_proj["renew"] = np.random.uniform(0, 1, len(hex_us_proj))                         # 0–1 renewable %
hex_us_proj["price"] = np.random.normal(loc=40, scale=10, size=len(hex_us_proj))         # wholesale $/MWh
hex_us_proj["load"] = np.random.normal(loc=200, scale=80, size=len(hex_us_proj))         # relative demand index
hex_us_proj["emissions"] = np.random.uniform(0.1, 0.9, len(hex_us_proj))                 # CO₂/MWh proxy
hex_us_proj["stability"] = np.random.uniform(0.7, 1.0, len(hex_us_proj))                 # grid stability 0–1

In [105]:
def normalize(col):
    return (col - col.min()) / (col.max() - col.min())

for col in ["temp", "renew", "price", "load", "emissions", "stability"]:
    hex_us_proj[f"n_{col}"] = normalize(hex_us_proj[col])

In [ ]:
profit = 0.40*(1 - n_price) + 0.35*n_load + 0.25*(1 - n_temp)
sustain = 0.45*n_renew + 0.35*n_stability + 0.20*(1 - n_emissions)
profit = 0.40*(1 - n_price) + 0.35*n_load + 0.25*(1 - n_temp)
sustain = 0.45*n_renew + 0.35*n_stability + 0.20*(1 - n_emissions)
datacenter_score = 0.6*profit + 0.4*sustain
hex_us_proj["profit"] = (
    0.40*(1 - hex_us_proj["n_price"]) +
    0.35*hex_us_proj["n_load"] +
    0.25*(1 - hex_us_proj["n_temp"])
)

hex_us_proj["sustain"] = (
    0.45*hex_us_proj["n_renew"] +
    0.35*hex_us_proj["n_stability"] +
    0.20*(1 - hex_us_proj["n_emissions"])
)

hex_us_proj["dc_score_raw"] = (
    0.6 * hex_us_proj["profit"] +
    0.4 * hex_us_proj["sustain"]
)

from sklearn.neighbors import NearestNeighbors

# get hex centroids
centers = np.vstack(hex_us_proj.geometry.centroid.apply(lambda p: (p.x, p.y)).values)

nbrs = NearestNeighbors(n_neighbors=7, algorithm='ball_tree').fit(centers)
distances, indices = nbrs.kneighbors(centers)

smoothed = []
raw = hex_us_proj["dc_score_raw"].values

for neigh in indices:
    smoothed.append(raw[neigh].mean())

hex_us_proj["dc_score"] = smoothed

hex_us = hex_us_proj.to_crs("EPSG:4326")

hex_us.explore(
    column="dc_score",
    cmap="YlOrRd",
    scheme="quantiles",
    legend=True,
    missing_kwds={"color": "#e0e0e0", "label": "No data"},
)

In [12]:
# ALL SYNTHETIC DATA, THIS IS JUST A PREVIEW OF WHAT THE MAP COULD POSSIBLY LOOK LIKE
np.random.seed(0)

hex_us_proj["price_raw"]     = np.random.normal(40, 10, len(hex_us_proj))
hex_us_proj["load_raw"]      = np.random.normal(200, 80, len(hex_us_proj))
hex_us_proj["temp_raw"]      = np.random.normal(60, 10, len(hex_us_proj))
hex_us_proj["renew_raw"]     = np.random.uniform(0, 1, len(hex_us_proj))
hex_us_proj["stability_raw"] = np.random.uniform(0.7, 1.0, len(hex_us_proj))
hex_us_proj["co2_raw"]       = np.random.uniform(200, 800, len(hex_us_proj))

for col in ["price_raw","load_raw","temp_raw","renew_raw","stability_raw","co2_raw"]:
    hex_us_proj["n_"+col] = (
        hex_us_proj[col] - hex_us_proj[col].min()
    ) / (hex_us_proj[col].max() - hex_us_proj[col].min())

hex_us_proj["profit"] = (
    0.40*(1 - hex_us_proj["n_price_raw"]) +
    0.35*(hex_us_proj["n_load_raw"]) +
    0.25*(1 - hex_us_proj["n_temp_raw"])
)

hex_us_proj["sustain"] = (
    0.45*(hex_us_proj["n_renew_raw"]) +
    0.35*(hex_us_proj["n_stability_raw"]) +
    0.20*(1 - hex_us_proj["n_co2_raw"])
)

hex_us_proj["dc_score_raw"] = (
    0.6 * hex_us_proj["profit"] +
    0.4 * hex_us_proj["sustain"]
)

from sklearn.neighbors import NearestNeighbors

centers = np.vstack(hex_us_proj.geometry.centroid.apply(lambda p: (p.x,p.y)))
nbrs = NearestNeighbors(n_neighbors=7).fit(centers)
d, idx = nbrs.kneighbors(centers)

smooth = np.array([hex_us_proj["dc_score_raw"].values[i].mean() for i in idx])
hex_us_proj["dc_score"] = smooth

hex_us = hex_us_proj.to_crs("EPSG:4326")
hex_us.explore(column="dc_score", cmap="YlOrRd", legend=True)

NameError: name 'hex_us_proj' is not defined